# A script that generates urls for iids from the ESGF API

I originally made all the API calls in the recipe generation, but that had several drawbacks:
- It would slow down the recipe generation by a lot, especially with an increasing number of iids
- It would make the recipe generation dependent on the ESGF API, which is flaky as hell.

So I decided to make a script that generates the urls for the iids, writes them to a more reliable database (BigQuery), and then the recipe generation can just read from that database.

## Notes

removing this from the runtime recipe generation should speed up submission by a lot!

- Only overwrite when forced? Later
- BigQuery Interface
    - Add row needs to be able to overwrite

- BigQuerySchema:
    - iid should be required
    

In [2]:
# from transforms import StoreToZarrLegacyDynamic as StoreToZarr
import json
# from pyesgf.search import SearchConnection # i am going back to pangeo-forge-esgf 
from bigquery import BigQueryInterface
from google.cloud import bigquery
from pangeo_forge_esgf import generate_urls_from_iids

In [4]:
iids = [
 # from https://github.com/Timh37/CMIP6cf/issues/2
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r17i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r2i3p1f1.day.pr.gn.v20201222',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r127i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r138i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r134i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r110i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r1i3p1f1.day.pr.gn.v20201222',
 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r4i3p1f1.day.pr.gn.v20201222',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r27i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r103i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r1i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r142i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r124i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r29i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r7i1p1f2.day.pr.gr.v20210218',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r2i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r4i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r111i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r126i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r136i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r20i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r122i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r131i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r7i1p1f2.day.sfcWind.gr.v20210218',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r24i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r1i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r133i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r13i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r141i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r19i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r30i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r18i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r123i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r8i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r121i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r23i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r146i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r16i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r2i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r149i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r23i1p1f1.day.psl.gr.v20200407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r145i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r29i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r2i1p1f3.day.psl.gn.v20200515',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r12i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r23i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r7i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r7i1p1f2.day.psl.gr.v20210218',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r14i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r132i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r9i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r118i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r21i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r13i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r115i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r26i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r129i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r6i1p1f2.day.sfcWind.gr.v20210517',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r12i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r113i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r106i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r12i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r114i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r6i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r128i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r12i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r17i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r147i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r17i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r27i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r4i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r21i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r101i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r130i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r2i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r150i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r19i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r17i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r108i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r144i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r21i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r10i1p1f2.day.psl.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r120i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r19i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r5i3p1f1.day.pr.gn.v20201222',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r5i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r125i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r18i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r29i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r28i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r10i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r1i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r112i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r8i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r30i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r30i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r10i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r143i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r139i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r10i1p1f2.day.sfcWind.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r8i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r137i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r19i1p1f2.day.sfcWind.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r23i1p1f2.day.pr.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r140i1p1f1.day.psl.gr.v20200412', # fails with depenency issues? (only intermittent)
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r148i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r27i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r119i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r105i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r8i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r116i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r11i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r15i1p1f1.day.pr.gn.v20200623',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r20i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r22i1p1f2.day.pr.gr.v20210407',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r117i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r107i1p1f1.day.psl.gr.v20200412',
 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r3i3p1f1.day.pr.gn.v20201222',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r16i1p1f1.day.pr.gn.v20200623',
 'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r4i1p1f1.day.pr.gn.v20190603',
 'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r5i1p1f1.day.pr.gn.v20190603',
 'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r2i1p1f1.day.pr.gn.v20190603',
 'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r3i1p1f1.day.pr.gn.v20190603',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r10i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r11i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r12i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r13i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r14i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r15i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r16i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r17i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r18i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r19i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r20i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r4i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r5i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r6i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r7i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r8i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r9i1p1f1.day.sfcWind.gn.v20200623'
#  # https://github.com/pangeo-forge/cmip6-feedstock/issues/22
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r19i1p1f2.Omon.zmeso.gn.v20200430',
#  'CMIP6.CMIP.CCCma.CanESM5-CanOE.historical.r2i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r4i1p1f2.Omon.zmeso.gn.v20200204',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r1i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r14i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM5A2-INCA.historical.r1i1p1f1.Omon.zmeso.gn.v20200729',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r27i1p1f1.Omon.zmeso.gn.v20191204',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r29i1p1f1.Omon.zmeso.gn.v20191204',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r3i1p1f2.Omon.zmeso.gn.v20190125',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r9i1p1f2.Omon.zmeso.gn.v20200117',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r10i1p1f2.Omon.zmeso.gn.v20200428',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r30i1p1f1.Omon.zmeso.gn.v20191204',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r33i1p1f1.Omon.zmeso.gn.v20211229',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r11i1p1f2.Omon.zmeso.gn.v20200408',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r31i1p1f1.Omon.zmeso.gn.v20191204',
#  'CMIP6.CMIP.CCCma.CanESM5-CanOE.historical.r3i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r17i1p1f2.Omon.zmeso.gn.v20200430',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r25i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.CCCma.CanESM5-CanOE.historical.r1i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.CMIP.CMCC.CMCC-ESM2.historical.r1i1p1f1.Omon.zmeso.gn.v20210114',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r9i1p1f2.Omon.zmeso.gn.v20200206',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r6i1p1f2.Omon.zmeso.gn.v20200117',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r7i1p1f2.Omon.zmeso.gn.v20200117',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-ESM4.historical.r1i1p1f1.Omon.zmeso.gr.v20190726',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r6i1p1f3.Omon.zmeso.gn.v20200204',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r15i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r11i1p1f2.Omon.zmeso.gn.v20200428',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r24i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r8i1p1f2.Omon.zmeso.gn.v20200204',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r28i1p1f1.Omon.zmeso.gn.v20191204',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r10i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r18i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r17i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r21i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r19i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r2i1p1f1.Omon.zmeso.gn.v20190305',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r12i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r16i1p1f2.Omon.zmeso.gn.v20200430',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r26i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r20i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r7i1p1f3.Omon.zmeso.gn.v20200204',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r2i1p1f2.Omon.zmeso.gn.v20200309',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r1i1p1f2.Omon.zmeso.gn.v20181206',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r2i1p1f2.Omon.zmeso.gn.v20190125',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r4i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r16i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r1i1p1f2.Omon.zmeso.gn.v20200123',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r3i1p1f2.Omon.zmeso.gn.v20200319',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r5i1p1f2.Omon.zmeso.gn.v20190125',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r22i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r18i1p1f2.Omon.zmeso.gn.v20200430',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r32i1p1f1.Omon.zmeso.gn.v20190802',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r8i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r23i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r3i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r5i1p1f3.Omon.zmeso.gn.v20200124',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r9i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r10i1p1f2.Omon.zmeso.gn.v20200117',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR-INCA.historical.r1i1p1f1.Omon.zmeso.gn.v20210216',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r8i1p1f2.Omon.zmeso.gn.v20200117',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r5i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.NIMS-KMA.UKESM1-0-LL.historical.r13i1p1f2.Omon.zmeso.gn.v20200805',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r13i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-ESM2-1.historical.r4i1p1f2.Omon.zmeso.gn.v20190125',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r6i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r7i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.IPSL.IPSL-CM6A-LR.historical.r11i1p1f1.Omon.zmeso.gn.v20180803',
#  'CMIP6.CMIP.MOHC.UKESM1-0-LL.historical.r12i1p1f2.Omon.zmeso.gn.v20200428',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp126.r6i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp126.r14i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r8i1p1f2.Omon.zmeso.gn.v20200415',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp126.r1i1p1f2.Omon.zmeso.gn.v20190328',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp126.r4i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r16i1p1f2.Omon.zmeso.gn.v20200710',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r5i1p1f2.Omon.zmeso.gn.v20201015',
#  'CMIP6.ScenarioMIP.CMCC.CMCC-ESM2.ssp126.r1i1p1f1.Omon.zmeso.gn.v20210126',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r1i1p1f2.Omon.zmeso.gn.v20200213',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r19i1p1f2.Omon.zmeso.gn.v20200716',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r4i1p1f2.Omon.zmeso.gn.v20211202',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp126.r4i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.NOAA-GFDL.GFDL-ESM4.ssp126.r1i1p1f1.Omon.zmeso.gr.v20180701',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp126.r1i1p1f1.Omon.zmeso.gn.v20190903',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r12i1p1f2.Omon.zmeso.gn.v20200710',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r6i1p1f2.Omon.zmeso.gn.v20201009',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp126.r5i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp126.r1i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r17i1p1f2.Omon.zmeso.gn.v20200710',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r9i1p1f2.Omon.zmeso.gn.v20200708',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r3i1p1f2.Omon.zmeso.gn.v20200310',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp126.r2i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r10i1p1f2.Omon.zmeso.gn.v20200706',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r11i1p1f2.Omon.zmeso.gn.v20200710',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp126.r3i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r18i1p1f2.Omon.zmeso.gn.v20200716',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp126.r2i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp126.r3i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r7i1p1f2.Omon.zmeso.gn.v20201015',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp126.r2i1p1f1.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp126.r2i1p1f2.Omon.zmeso.gn.v20200310',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM5A2-INCA.ssp126.r1i1p1f1.Omon.zmeso.gn.v20220105',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp126.r3i1p1f1.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r11i1p1f1.Omon.zmeso.gn.v20191003',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r22i1p1f1.Omon.zmeso.gn.v20200218',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp245.r2i1p1f2.Omon.zmeso.gn.v20200415',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r2i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r10i1p1f1.Omon.zmeso.gn.v20191003',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r5i1p1f1.Omon.zmeso.gn.v20191003',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r8i1p1f2.Omon.zmeso.gn.v20201028',
#  'CMIP6.ScenarioMIP.CMCC.CMCC-ESM2.ssp245.r1i1p1f1.Omon.zmeso.gn.v20210129',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp245.r2i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r25i1p1f1.Omon.zmeso.gn.v20200218',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r6i1p1f2.Omon.zmeso.gn.v20201028',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r1i1p1f2.Omon.zmeso.gn.v20190328',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r10i1p1f2.Omon.zmeso.gn.v20201028',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp245.r3i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r2i1p1f1.Omon.zmeso.gn.v20190516',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r5i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp245.r4i1p1f2.Omon.zmeso.gn.v20200721',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r14i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r9i1p1f2.Omon.zmeso.gn.v20201028',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r1i1p1f1.Omon.zmeso.gn.v20190119',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r3i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r4i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r3i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp245.r6i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r7i1p1f2.Omon.zmeso.gn.v20201028',
#  'CMIP6.ScenarioMIP.NOAA-GFDL.GFDL-ESM4.ssp245.r1i1p1f1.Omon.zmeso.gr.v20180701',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp245.r1i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp245.r1i1p1f2.Omon.zmeso.gn.v20200415',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp245.r3i1p1f2.Omon.zmeso.gn.v20200721',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp245.r4i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp245.r8i1p1f2.Omon.zmeso.gn.v20200721',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r3i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp585.r4i1p1f2.Omon.zmeso.gn.v20211201',
#  'CMIP6.ScenarioMIP.NOAA-GFDL.GFDL-ESM4.ssp585.r1i1p1f1.Omon.zmeso.gr.v20180701',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r4i1p1f1.Omon.zmeso.gn.v20191122',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r33i1p1f1.Omon.zmeso.gn.v20211229',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp585.r3i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp585.r1i1p1f2.Omon.zmeso.gn.v20200415',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp585.r2i1p1f2.Omon.zmeso.gn.v20200420',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp585.r4i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp585.r1i1p1f2.Omon.zmeso.gn.v20191021',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp585.r2i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r14i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp585.r3i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.CMCC.CMCC-ESM2.ssp585.r1i1p1f1.Omon.zmeso.gn.v20210126',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r1i1p1f1.Omon.zmeso.gn.v20190903',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-ESM2-1.ssp585.r5i1p1f2.Omon.zmeso.gn.v20190410',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp585.r3i1p1f2.Omon.zmeso.gn.v20200721',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp585.r1i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.CCCma.CanESM5-CanOE.ssp585.r2i1p2f1.Omon.zmeso.gn.v20190429',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r2i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.r6i1p1f1.Omon.zmeso.gn.v20191121',
#  'CMIP6.ScenarioMIP.MOHC.UKESM1-0-LL.ssp585.r8i1p1f2.Omon.zmeso.gn.v20200721'
#  # https://github.com/pangeo-forge/cmip6-feedstock/issues/20
#  'CMIP6.CMIP.THU.CIESM.piControl.r1i1p1f1.Omon.uo.gn.v20200220',
#  'CMIP6.CMIP.THU.CIESM.piControl.r1i1p1f1.Omon.vo.gn.v20200220',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.so.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.hfds.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.wfo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.tauuo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.tauvo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.umo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.vmo.gn.v20191021',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-CM6-1-HR.ssp126.r1i1p1f2.Omon.uo.gn.v20200127',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-CM6-1-HR.ssp126.r1i1p1f2.Omon.umo.gn.v20200127',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.wfo.gn.v20191125',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.uo.gn.v20191126',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.uo.gn.v20191125',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.vo.gn.v20191126',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.umo.gn.v20191126',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.vmo.gn.v20191126',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.uo.gn.v20180701',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.vo.gn.v20180701',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.tauuo.gn.v20180701',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.tauvo.gn.v20180701',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.historical.r1i1p1f3.Omon.vmo.gn.v20191216',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.hfds.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.wfo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.uo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.vo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.tauuo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.tauvo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.umo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.vmo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.hfds.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.wfo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.uo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.vo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.tauuo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.tauvo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.umo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.vmo.gn.v20200515',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.thetao.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.so.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.hfds.gn.v20191204',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.uo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.vo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.tauuo.gn.v20191204',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.tauvo.gn.v20191204',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.umo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.vmo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Amon.psl.gn.v20190920',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.hfds.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.wfo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.tauuo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.hfds.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.wfo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.tauuo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.hfds.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.wfo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.tauuo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.historical.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.umo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.vmo.gn.v20210129',
#  'CMIP6.CMIP.MPI-M.MPI-ESM1-2-HR.historical.r1i1p1f1.Omon.so.gn.v20190710',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r1i1p1f1.Omon.uo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r1i1p1f1.Omon.vo.gn.v20210311',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.hfds.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.wfo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.tauuo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.tauvo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.hfds.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.wfo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.tauuo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.tauvo.gn.v20210329',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.thetao.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.so.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.hfds.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.wfo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.uo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.vo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.tauuo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.tauvo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.umo.gn.v20191224',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.vmo.gn.v20191224',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.hfds.gn.v20190815',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.wfo.gn.v20190815',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.umo.gn.v20190815',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.vmo.gn.v20190815''CMIP6.CMIP.THU.CIESM.piControl.r1i1p1f1.Omon.uo.gn.v20200220',
#  'CMIP6.CMIP.THU.CIESM.piControl.r1i1p1f1.Omon.vo.gn.v20200220',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.so.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.hfds.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.wfo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.tauuo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.tauvo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.umo.gn.v20191021',
#  'CMIP6.CMIP.CNRM-CERFACS.CNRM-CM6-1-HR.historical.r1i1p1f2.Omon.vmo.gn.v20191021',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-CM6-1-HR.ssp126.r1i1p1f2.Omon.uo.gn.v20200127',
#  'CMIP6.ScenarioMIP.CNRM-CERFACS.CNRM-CM6-1-HR.ssp126.r1i1p1f2.Omon.umo.gn.v20200127',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.wfo.gn.v20191125',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.uo.gn.v20191126',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.uo.gn.v20191125',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.vo.gn.v20191126',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.umo.gn.v20191126',
#  'CMIP6.CMIP.CAS.FGOALS-g3.piControl.r1i1p1f1.Omon.vmo.gn.v20191126',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.uo.gn.v20180701',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.vo.gn.v20180701',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.tauuo.gn.v20180701',
#  'CMIP6.CMIP.NOAA-GFDL.GFDL-CM4.piControl.r1i1p1f1.Omon.tauvo.gn.v20180701',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.historical.r1i1p1f3.Omon.vmo.gn.v20191216',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.hfds.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.wfo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.uo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.vo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.tauuo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.tauvo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.umo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp126.r1i1p1f3.Omon.vmo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.hfds.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.wfo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.uo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.vo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.tauuo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.tauvo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.umo.gn.v20200515',
#  'CMIP6.ScenarioMIP.MOHC.HadGEM3-GC31-MM.ssp585.r1i1p1f3.Omon.vmo.gn.v20200515',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.thetao.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.so.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.hfds.gn.v20191204',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.uo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.vo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.tauuo.gn.v20191204',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.tauvo.gn.v20191204',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.umo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Omon.vmo.gn.v20200107',
#  'CMIP6.CMIP.MOHC.HadGEM3-GC31-MM.piControl.r1i1p1f1.Amon.psl.gn.v20190920',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.hfds.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.wfo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.tauuo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.hfds.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.wfo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.tauuo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp126.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.hfds.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.wfo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.tauuo.gn.v20210129',
#  'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp585.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.historical.r1i1p1f1.Omon.tauvo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.umo.gn.v20210129',
#  'CMIP6.CMIP.MIROC.MIROC6.piControl.r1i1p1f1.Omon.vmo.gn.v20210129',
#  'CMIP6.CMIP.MPI-M.MPI-ESM1-2-HR.historical.r1i1p1f1.Omon.so.gn.v20190710',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r1i1p1f1.Omon.uo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.historical.r1i1p1f1.Omon.vo.gn.v20210311',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.hfds.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.wfo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.tauuo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp126.r1i1p1f1.Omon.tauvo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.hfds.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.wfo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.tauuo.gn.v20210329',
#  'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp585.r1i1p1f1.Omon.tauvo.gn.v20210329',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.thetao.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.so.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.hfds.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.wfo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.uo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.vo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.tauuo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.tauvo.gn.v20210311',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.umo.gn.v20191224',
#  'CMIP6.CMIP.MRI.MRI-ESM2-0.piControl.r1i1p1f1.Omon.vmo.gn.v20191224',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.hfds.gn.v20190815',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.wfo.gn.v20190815',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.umo.gn.v20190815',
#  'CMIP6.CMIP.NCC.NorESM2-LM.historical.r1i1p1f1.Omon.vmo.gn.v20190815'
       ]

## Batch query ESGF for the urls

In [5]:
url_dict = await generate_urls_from_iids(iids)

iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r17i1p1f2.day.sfcWind.gr.v20201015': Requesting data from search node https://esgf-data.dkrz.de/esg-search/search
iid='CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r2i3p1f1.day.pr.gn.v20201222': Requesting data from search node https://esgf-data.dkrz.de/esg-search/search
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015': Requesting data from search node https://esgf-data.dkrz.de/esg-search/search
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r127i1p1f1.day.psl.gr.v20200412': Requesting data from search node https://esgf-data.dkrz.de/esg-search/search
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r138i1p1f1.day.psl.gr.v20200412': Requesting data from search node https://esgf-data.dkrz.de/esg-search/search
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.sfcWind.gr.v20201015': Requesting data from search node https://esgf-data.dkrz.de/esg-s

In [6]:
url_dict.keys()

dict_keys(['CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r2i3p1f1.day.pr.gn.v20201222', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.sfcWind.gr.v20201015', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r134i1p1f1.day.psl.gr.v20200412', 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r1i3p1f1.day.pr.gn.v20201222', 'CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r4i3p1f1.day.pr.gn.v20201222', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r27i1p1f2.day.sfcWind.gr.v20201015', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r1i1p1f2.day.pr.gr.v20201015', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r7i1p1f2.day.pr.gr.v20210218', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r2i1p1f2.day.sfcWind.gr.v20201015', 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r4i1p1f1.day.pr.gn.v20200623', 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.pr

In [7]:
table_id = 'leap-pangeo.testcmip6.stores_v2'
client = bigquery.Client()
bq_interface = BigQueryInterface(client, table_id)

In [8]:
## Query ESGF for the urls

# conn = SearchConnection(
#     "https://esgf-node.llnl.gov/esg-search",
#     distrib=True
# )

overwrite=False

for iid in iids:
    iid_obj = bq_interface.get_iid_results(iid)
    if iid_obj.has_urls and not overwrite:
        print(f"{iid=}: Is already in the database")
    else:

        if iid not in url_dict.keys():
            # this will only write the iid to bigquery
            print(f"{iid=}: No URLs available to parse")
        else:
            fields = {'urls': dd}
        errors = bq_interface.add_row(iid_obj, fields = fields, force=False) # since this is the first step, should I be force overwriting?
        
        assert len(errors) == 0


        # print(f"{iid=}: Querying ESGF for urls")
        # try:
        #     fields = esgf_url_request(iid_obj.iid, conn)
        #     if 'urls' not in fields.keys():
        #         # if url extraction fails write only the iid into bigquery
        #         print(f"{iid}: Could not find any URLs")
        #     errors = bq_interface.add_row(iid_obj, fields = fields, force=False) # since this is the first step, should I be force overwriting?
        #     assert len(errors) == 0
        # except Exception as e:
        #     print(f'{iid}: Failed with {e}')

iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r17i1p1f2.day.sfcWind.gr.v20201015': Is already in the database
iid='CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.r2i3p1f1.day.pr.gn.v20201222': Is already in the database
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015': Is already in the database
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r127i1p1f1.day.psl.gr.v20200412': Is already in the database
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r138i1p1f1.day.psl.gr.v20200412': Is already in the database
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r15i1p1f2.day.sfcWind.gr.v20201015': Is already in the database
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r134i1p1f1.day.psl.gr.v20200412': Is already in the database
iid='CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp585.r110i1p1f1.day.psl.gr.v20200412': Is already in the database
iid='CMIP6.ScenarioMIP.MRI.MRI-ESM2-0.ssp245.

NameError: name 'dd' is not defined

In [ ]:
# these bits could be useful for pangeo-forge-esgf
# especially the IID schema bit (which we could then use to support other data like cordex)
import pyesgf
from typing import Dict

IID_SCHEMA = 'mip_era.activity_id.institution_id.source_id.experiment_id.member_id.table_id.variable_id.grid_label.version'


def esgf_url_request(iid: str, conn:pyesgf.search.connection.SearchConnection) -> Dict[str, str]:
    """return a dict of query results for a given instance_id via a query to the ESGF API"""
    context_kwargs = {'replica':None,'facets':['doi']} # this assumes that I can use replicas just like master records. I think that is fine
    for label, value in zip(IID_SCHEMA.split('.'), iid.split('.')):
        context_kwargs[label] = value

    # is this a problem with the `v...` in version?
    context_kwargs['version'] = context_kwargs['version'].replace('v','')

    # testing
    # del context_kwargs['version']
    ctx = conn.new_context(**context_kwargs)
    # print(f"{iid}: Found {ctx.hit_count} hits")

    results = ctx.search(facets='*') # these might include several data nodes (curiously even if I set replica to false?)
    fields = {}
    # for now take the first one that has any urls at all
    for ri,result in enumerate(results):
        print(f"{iid}-{result.dataset_id}: Extracting URLS")
        urls = [f.download_url for f in result.file_context().search(facets='*')] # this raises an annoying warning each time. FIXME

        if len(urls)>0:
            # add fields to BigQuery
            fields['urls'] = urls
            instance_id_check, fields['data_node'] = result.dataset_id.split('|')
            assert instance_id_check == iid
            # break after the first successful url extraction
            break
        else:
            # if url extraction fails write only the iid into bigquery
            print(f"{iid}: Could not find any URLs")
            
    return fields

In [7]:
# conn = SearchConnection(
#     "https://esgf-node.llnl.gov/esg-search",
#     distrib=True
# )

## Check iids that could not get a url
Still working on this..Now dinner

In [23]:
query= f"""
SELECT instance_id, timestamp
FROM `{table_id}`
WHERE urls IS NULL OR ARRAY_LENGTH(urls) = 0
AND instance_id IN (
    SELECT instance_id
    FROM `{table_id}`
    GROUP BY instance_id
    ORDER BY timestamp
)
"""

In [24]:
# query = f"""
# WITH (SELECT * FROM `{table_id}` ORDER BY timestamp DESC) AS latest
# SELECT *
# FROM latest
# WHERE urls IS NULL OR ARRAY_LENGTH(urls) = 0
# """
query_job = client.query(query)  # Make an API request.
# # this should never return more than one row or something has gone really wrong?
# # TODO: This might have to be revisited when I overwrite stuff
# [urls] = [row['urls'] for row in query_job]
# return urls

# client.

In [25]:
query_job.errors

[{'reason': 'invalidQuery',
  'location': 'query',
  'message': 'ORDER BY clause expression references column timestamp which is neither grouped nor aggregated at [9:14]'}]

In [16]:
missing_url_iids = []
for row in query_job:
    missing_url_iids.append(row['instance_id'])

In [17]:
missing_url_iids

['CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015',
 'CMIP6.ScenarioMIP.EC-Earth-Consortium.EC-Earth3.ssp245.r25i1p1f2.day.psl.gr.v20201015']

In [15]:
import gcsfs
import json
with open('/Users/juliusbusecke/Downloads/keys/leap-pangeo-dataflow_service_account.json') as f:
    token = json.load(f)
fs = gcsfs.GCSFileSystem(token=token) # auth here...

for k,v in recipe_input_dict.items():
    with open(f"{k}.json", 'w') as file:
        json.dump(v, file)
    fs.put(f"{k}.json", f"gs://leap-persistent/jbusecke/cmip6urls/{k}.json")

In [16]:
set(iids) - set(recipe_input_dict.keys())

{'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r10i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r11i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r12i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r13i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r14i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r15i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r16i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r17i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r18i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r19i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r20i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r4i1p1f1.day.sfcWind.gn.v20200623',
 'CMIP6.ScenarioMIP.MIROC.MIROC6.ssp245.r5i1p1f1.day.sfcWind.gn.v20200623',
 

In [17]:
# list(recipe_input_dict.keys())

In [ ]:
client.update_table(